Esta notebook contiene bloques de código útiles para realizar Q-learning en el entorno "Pendulum"

In [1]:
import numpy as np
from pendulum_env_extended import PendulumEnvExtended
import random 

In [2]:
alpha = 0.1
gamma = 0.99
epsilon = 0.1
n_episodes = 100
epsilon_variability = 0.8

In [3]:
env = PendulumEnvExtended(render_mode='rgb_array')

Discretización de los estados

In [4]:
x_space = np.linspace(-1, 1, 10)
y_space = np.linspace(-1, 1, 10)
vel_space = np.linspace(-8, 8, 100)
x_space

array([-1.        , -0.77777778, -0.55555556, -0.33333333, -0.11111111,
        0.11111111,  0.33333333,  0.55555556,  0.77777778,  1.        ])

Obtener el estado a partir de la observación

In [5]:
def get_state(obs):
    x, y, vel = obs
    x_bin = np.digitize(x, x_space)
    y_bin = np.digitize(y, y_space)
    vel_bin = np.digitize(vel, vel_space)
    return x_bin, y_bin, vel_bin

In [6]:
state = get_state(np.array([-0.4, 0.2, 0.3])) #mapeo de estado. Nos dice el bin en el que estamos
state

(3, 6, 52)

Discretización de las acciones

In [7]:
actions = list(np.linspace(-2, 2, 10)) #minimo, maximo y cuantos bins
actions

[-2.0,
 -1.5555555555555556,
 -1.1111111111111112,
 -0.6666666666666667,
 -0.22222222222222232,
 0.22222222222222232,
 0.6666666666666665,
 1.1111111111111107,
 1.5555555555555554,
 2.0]

In [8]:
def get_sample_action():
    return np.array([random.choice(actions)], dtype=np.float32)

Inicilización de la tabla Q

In [9]:
Q = np.zeros((len(x_space) + 1, len(y_space) + 1, len(vel_space) + 1, len(actions)))
Q

array([[[[0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         ...,
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.]],

        [[0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         ...,
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.]],

        [[0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         ...,
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.]],

        ...,

        [[0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         ...,
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
    

Obtención de la acción a partir de la tabla Q

In [10]:
def optimal_policy(state, Q):
    action = np.argmax(Q[state])
    return action

Epsilon-Greedy Policy

In [11]:
def epsilon_greedy_policy(state, Q, epsilon=0.1):
    explore = np.random.binomial(1, epsilon)
    # explore
    if explore:
        action = get_sample_action()
        print('explore')
    # exploit
    else:
        action = np.array([np.argmax(Q[get_state(state)])], dtype=np.int32)
        print('exploit')
        
    return action

Ejemplo de episodio 

In [12]:
obs,_ = env.reset()
print(obs)
done = False
total_reward = 0
while not done:
    state = get_state(obs)
    print('state', state)
    action = epsilon_greedy_policy(state, Q, 0.5)
    obs, reward, done, _, _ = env.step(action)
    total_reward += reward
    print('->', state, action, reward, obs, done)
    env.render()
print('total_reward', total_reward)

[-0.9154359  -0.40246373  0.13629633]
state (1, 3, 51)
explore
-> (1, 3, 51) [-1.1111112] -7.441726956046317 [-0.9219946  -0.3872027  -0.33221814] False


DependencyNotInstalled: pygame is not installed, run `pip install gymnasium[classic-control]`

In [ ]:
def train_policy(alpha, gamma, epsilon, epsilon_variability, episodes):

            total_rewards = []

            for episode in range(episodes):
                obs, _ = env.reset()
                done = False
                total_reward = 0
                step_count = 0

                while not done:
                    state = obs
                    epsilon = max(epsilon - epsilon_variability * epsilon, 0)  # Decay epsilon
                    action = epsilon_greedy_policy(state, Q, epsilon)
                    obs, reward, done, _, _ = env.step(action)
                    print(state)
                    print(reward)
                    print(action)
                    newState = get_state(state)
                    Q[newState[0],newState[1],newState[2],action] = Q[newState[0],newState[1],newState[2],action] + alpha * (reward + gamma * np.max(Q[get_state(obs)]) - Q[newState[0],newState[1],newState[2],action])
                    #Q[state, action] = Q[state, action] + alpha * (reward + gamma * np.max(Q[obs]) - Q[state, action])
                    total_reward += reward
                    step_count += 1

                total_rewards.append(total_reward)
                print(f" total reward: {total_reward}, steps: {step_count}")


In [ ]:
train_policy(alpha, gamma, epsilon, epsilon_variability, n_episodes)

exploit
[-0.7034014  -0.71079284 -0.6819555 ]
-5.573556547216967
[0]
exploit
[-0.7452596 -0.6667744 -1.2150502]
-5.96403016571281
[0]
exploit
[-0.7996311 -0.6004915 -1.7151309]
-6.531558725807549
[0]
exploit
[-0.85983974 -0.5105641  -2.1654997 ]
-7.2588821783608015
[0]
exploit
[-0.91774964 -0.39715937 -2.5484226 ]
-8.119681015608023
[0]
exploit
[-0.9648025  -0.26297548 -2.8462923 ]
-9.078567507853924
[0]
exploit
[-0.99351716 -0.11368245 -3.0435238 ]
-10.093052420667027
[0]
exploit
[-0.9990966   0.04249773 -3.1287856 ]
-10.583239965518954
[0]
exploit
[-0.9805884  0.1960775 -3.0969124]
-9.627615209494476
[0]
exploit
[-0.9411266   0.33805445 -2.9498541 ]
-8.691939847306596
[0]
exploit
[-0.8871498  0.4614816 -2.6963134]
-7.812871932074652
[0]
exploit
[-0.82692766  0.5623084  -2.3502023 ]
-7.026408068433098
[0]
exploit
[-0.76895064  0.63930815 -1.928471  ]
-6.364576923284168
[0]
exploit
[-0.7206564  0.6932924 -1.4489899]
-5.853171077689234
[0]
exploit
[-0.6876865   0.72600776 -0.9290205 ]
-

In [ ]:
#alpha = 0.1  # Tasa de aprendizaje
#gamma = 0.99  # Factor de descuento
#epsilon = 0.1  # Tasa de exploración

#num_episodes = 1000

for episode in range(n_episodes):
    obs, _ = env.reset()
    done = False
    total_reward = 0

    while not done:
        state = get_state(obs)
        action = epsilon_greedy_policy(state, Q, epsilon) #Elije una acción
        next_obs, reward, done, _, _ = env.step(action) #Obtengo la recompensa
        next_state = get_state(next_obs)
        
        best_next_action = np.argmax(Q[next_state])
        td_target = reward + gamma * Q[next_state][best_next_action] #Calcula el target para la diferencia temporal
        td_error = td_target - Q[state][np.argmax(action)]
        Q[state][np.argmax(action)] += alpha * td_error
        
        obs = next_obs
        total_reward += reward

    print(f'Episode {episode + 1}: Total Reward: {total_reward}')


exploit
explore
exploit
exploit
exploit
explore
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
explore
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit


exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
explore
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
exploit
